 # download loom files via api 
 
### see api documentation
[documentation](https://service.azul.data.humancellatlas.org/)

In [2]:
import requests
import os
from tqdm import tqdm
import json
import pandas as pd
from tabulate import tabulate

In [68]:
# example function, downloading a single file which was specified before 
# modified! 
# TODO make this function work. Add file name to output_pat (see example code)

def download_file(index, output_path, files_list):
    for i in index: 

        url_tp = files_list[i]['url']
        url = url_tp.replace('/fetch', '')  # Work around https://github.com/DataBiosphere/azul/issues/2908
    
        response = requests.get(url, stream=True)
        response.raise_for_status()
    
        total = int(response.headers.get('content-length', 0))
        print(f'Downloading to: {output_path}', flush=True)
    
        with open(output_path, 'wb') as f:
            with tqdm(total=total, unit='B', unit_scale=True, unit_divisor=1024) as bar:
                for chunk in response.iter_content(chunk_size=1024):
                    size = f.write(chunk)
                    bar.update(size)



In [8]:
project_uuid = '4a95101c-9ffc-4f30-a809-f04518a23803'
catalog = 'dcp26'
endpoint_url = f'https://service.azul.data.humancellatlas.org/index/projects/{project_uuid}'

save_location = '/home/fran/Documents/AAMasterDataScience/BigDataPraktikum/data'

In [57]:
# example downoading of a project

response = requests.get(endpoint_url, params={'catalog': catalog,})
response.raise_for_status()
response_json = response.json()
project = response_json['projects'][0]

file_urls = set()
for key in ('matrices', 'contributedAnalyses'):
    tree = project[key]
    for path, file_info in iterate_matrices_tree(tree):
        url = file_info['url']
        if url not in file_urls:
            dest_path = os.path.join(save_location, file_info['name'])
            # TODO uncomment the folllowing line if you really want to download data: 
            # download_file(url, dest_path)
            file_urls.add(url)
print('Downloads Complete.')



Downloads Complete.


In [72]:
# function gets meta data of loom files
# TODO make default params and abiltiy to passing params to the function
def get_files_metadata():
    params = {
        'catalog': 'dcp26',
        'filters': '{"fileFormat": {"is": ["loom","loom.gz"]}}',
        'size': 10,
        'sort': 'lastModifiedDate',
        'order': 'asc'
    }
    url = f'https://service.azul.data.humancellatlas.org/index/files'
    response = requests.get(url, params=params)

    # Check the response status code
    if response.status_code == 200:
        # Request was successful
        response_json = response.json()
        return response_json
    else:
        # An error occurred
        print("Error:", response.status_code)

In [74]:

def get_file_list(response_json):
    # extract file-information into a list of dicts
    file_data = []  #list
    for hit in response_json['hits']:
        for file in hit['files']:
            file_dict = {
                'fileName':file['name'],
                'size':file['size'],
                'version':file['version'],
                'projectShortname':hit['projects'][0]['projectShortname'][0],
                'projectId':hit['projects'][0]['projectId'][0],
                'entryId':hit['entryId'],
                'contentDescription':file['contentDescription'][0],
                'url':file['url']
            }
            file_data.append(file_dict)
    file_data_with_index = [{
        'index': i,
        **file_dict
    } for i, file_dict in enumerate(file_data)]
    return file_data_with_index

def print_file_table(response_json):

    #file_data = get_file_list(response_json)
    file_data = response_json
    
    # create nested list out of file_data
    headers = ["Index", "File Name" , "Size", "Version", "Project (shortname)", "ProjectID", 
               "EntryId", "Content Description"]
    table_data = [[
        file['index'],
        file['fileName'],
        file['size'],
        file['version'],
        file['projectShortname'],
        file['projectId'],
        file['entryId'],
        file['contentDescription'],
    ] for file in file_data]

    table = tabulate(table_data, headers, tablefmt='fancy_grid')
    print(table)


In [75]:
# example workflow
# get file metadata 
antwort = get_files_metadata()
# transform & print it as list
files_list = get_file_list(antwort)
print_file_table(files_list)
# specifiy which file(s) you want to download (provide index-list)
index = [6]
catalog = 'dcp26'
save_location = '/home/fran/Documents/AAMasterDataScience/BigDataPraktikum/data'

download_file(index, save_location,files_list)


╒═════════╤═══════════════════════════════════════════╤════════════╤═════════════════════════════╤════════════════════════════╤══════════════════════════════════════╤══════════════════════════════════════╤═══════════════════════╕
│   Index │ File Name                                 │       Size │ Version                     │ Project (shortname)        │ ProjectID                            │ EntryId                              │ Content Description   │
╞═════════╪═══════════════════════════════════════════╪════════════╪═════════════════════════════╪════════════════════════════╪══════════════════════════════════════╪══════════════════════════════════════╪═══════════════════════╡
│       0 │ 098cc66a-d806-42db-a1c8-fa99a0317d7c.loom │  854692581 │ 2021-02-03T19:43:20.000000Z │ HumanTissueTcellActivation │ 4a95101c-9ffc-4f30-a809-f04518a23803 │ 131ea511-25f7-5801-993f-bfa25f8ca68d │ Count Matrix          │
├─────────┼───────────────────────────────────────────┼────────────┼────────────

IsADirectoryError: [Errno 21] Is a directory: '/home/fran/Documents/AAMasterDataScience/BigDataPraktikum/data'

## Weiterführende Notizen

https://www.askpython.com/python/examples/pull-data-from-an-api

Loom Dateien: 

Umgang mit LoomPy: 

https://linnarssonlab.org/loompy/apiwalkthrough/index.html